In [1]:
import torch 
import gpytorch 
import geometric_kernels.torch
import plotly.io as pio
from plotly import graph_objects as go
from plotly.subplots import make_subplots
from geometric_kernels.spaces import Hypersphere
from mdgp.models.deep_gps import EuclideanDeepGPLayer
from mdgp.utils import sphere_meshgrid, sphere_uniform_grid, spherical_harmonic


torch.set_default_dtype(torch.float64)
pio.templates.default = "plotly_dark"

/home/kacperwyrwal/miniconda3/envs/mdgp_requirements_test7/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
INFO: Using numpy backend


In [5]:
DIM = 2
SPACE = Hypersphere(DIM)
NUM_EIGENFUNCTIONS = 20
OUTPUT_DIMS = 3
NU = 0.5
NUM_INDUCING = 60 
INDUCING_POINTS = sphere_uniform_grid(NUM_INDUCING)
LEARN_INDUCING_LOCATIONS = False
OPTIMIZE_NU = False

layer = EuclideanDeepGPLayer(
    num_eigenfunctions=NUM_EIGENFUNCTIONS,
    output_dims=OUTPUT_DIMS,
    inducing_points=INDUCING_POINTS,
    nu=NU,
    learn_inducing_locations=LEARN_INDUCING_LOCATIONS,
    optimize_nu=OPTIMIZE_NU,
    whitened_variational_strategy=True, 
)

In [6]:
def target_fnc(x):
    return torch.stack([spherical_harmonic(x, 2, 3), spherical_harmonic(x, 1, 2), torch.ones(x.shape[:-1])], dim=-1)


test_inputs = sphere_meshgrid(100, 100)
test_targets = target_fnc(test_inputs)

train_inputs = sphere_uniform_grid(200)
train_targets = target_fnc(train_inputs)

In [8]:
with torch.no_grad():
    posterior_sample = layer(test_inputs.view(-1, 3), sample='pathwise', are_samples=False)


fig = make_subplots(rows=1, cols=3, specs=[[{'type': 'surface'}]*3], 
                    subplot_titles=["Posterior Sample 1", "Posterior Sample 2", "Posterior Sample 3"]) 

dim = 0
x, y, z = test_inputs.unbind(-1)
for i in range(1, 4): 
    fig.add_trace(
        go.Surface(
            x=x, 
            y=y,
            z=z,
            surfacecolor=posterior_sample[i, ..., dim].view_as(x),
            coloraxis="coloraxis",
        ),
        row=1, col=i
    )

fig.update_layout(
    coloraxis=dict(
        colorscale="plasma", 
    )
)

fig.show()